In [1]:
import pandas as pd
import numpy as np
import ast
import re
import plotly.express as px
import plotly.graph_objects as go

In [2]:
cols_march = [
    "appid","name","release_date","required_age","price","dlc_count","detailed_description",
    "about_the_game","short_description","reviews","header_image","website","support_url",
    "support_email","windows","mac","linux","metacritic_score","metacritic_url","achievements",
    "recommendations","notes","supported_languages","full_audio_languages","packages",
    "developers","publishers","categories","genres","screenshots","movies","user_score",
    "score_rank","positive","negative","estimated_owners","average_playtime_forever",
    "average_playtime_2weeks","median_playtime_forever","median_playtime_2weeks","discount",
    "peak_ccu","tags","pct_pos_total","num_reviews_total","pct_pos_recent","num_reviews_recent"
]

cols_may = [
    "AppID","name","release_date","required_age","price","dlc_count","detailed_description",
    "about_the_game","short_description","reviews","header_image","website","support_url",
    "support_email","windows","mac","linux","metacritic_score","metacritic_url","achievements",
    "recommendations","notes","supported_languages","full_audio_languages","packages",
    "developers","publishers","categories","genres","screenshots","movies","user_score",
    "score_rank","positive","negative","estimated_owners","average_playtime_forever",
    "average_playtime_2weeks","median_playtime_forever","median_playtime_2weeks","peak_ccu",
    "tags","pct_pos_total","num_reviews_total","pct_pos_recent","num_reviews_recent"
]

df_march = pd.read_csv("games_march2025_cleaned.csv", header=0, names=cols_march)
df_may = pd.read_csv("games_may2024_cleaned.csv", header=0, names=cols_may)
df_may = df_may.rename(columns={"AppID": "appid"})
df_may["discount"] = 0

master_order = cols_march
df_may = df_may[master_order]
df_all = pd.concat([df_march, df_may], ignore_index=True)

print(df_all.shape)
print(df_all["appid"].nunique(), "unique apps")
print(df_all.isnull().mean().sort_values(ascending=False).head(10))

df_all = df_all.drop_duplicates(subset="appid", keep="first")
df_all.to_csv("games_march_to_may_2024_2025_merged.csv", index=False)
df = df_all

(173264, 47)
98528 unique apps
score_rank              0.999538
metacritic_url          0.956788
reviews                 0.880621
notes                   0.821936
website                 0.533233
support_url             0.502545
support_email           0.123505
about_the_game          0.002355
detailed_description    0.002095
short_description       0.001322
dtype: float64


In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 98528 entries, 0 to 173248
Data columns (total 47 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   appid                     98528 non-null  int64  
 1   name                      98525 non-null  object 
 2   release_date              98528 non-null  object 
 3   required_age              98528 non-null  int64  
 4   price                     98528 non-null  float64
 5   dlc_count                 98528 non-null  int64  
 6   detailed_description      98305 non-null  object 
 7   about_the_game            98282 non-null  object 
 8   short_description         98385 non-null  object 
 9   reviews                   11165 non-null  object 
 10  header_image              98528 non-null  object 
 11  website                   44742 non-null  object 
 12  support_url               48004 non-null  object 
 13  support_email             86199 non-null  object 
 14  windows   

In [4]:
df.describe()

appid  required_age         price     dlc_count  \
count  9.852800e+04  98528.000000  98528.000000  98528.000000   
mean   1.649300e+06      0.199456      7.323752      0.575775   
std    8.947109e+05      1.801254     13.230560     14.672119   
min    1.000000e+01     -1.000000      0.000000      0.000000   
25%    8.905850e+05      0.000000      0.990000      0.000000   
50%    1.575460e+06      0.000000      4.990000      0.000000   
75%    2.367620e+06      0.000000      9.990000      0.000000   
max    3.542350e+06     21.000000    999.980000   3427.000000   

       metacritic_score  achievements  recommendations    user_score  \
count      98528.000000  98528.000000     9.852800e+04  98528.000000   
mean           3.047134     19.766686     9.792180e+02      0.031808   
std           14.812261    156.188230     2.121478e+04      1.600575   
min            0.000000      0.000000     0.000000e+00      0.000000   
25%            0.000000      0.000000     0.000000e+00      0.000000   
50%            0.000000      4.000000     0.000000e+00      0.000000   
75%            0.000000     20.000000     0.000000e+00      0.000000   
max           97.000000   9821.000000     4.401572e+06    100.000000   

       score_rank      positive  ...  average_playtime_forever  \
count   41.000000  9.852800e+04  ...              9.852800e+04   
mean    99.170732  1.228685e+03  ...              1.102106e+02   
std      0.703649  3.054515e+04  ...              6.503189e+03   
min     98.000000  0.000000e+00  ...              0.000000e+00   
25%     99.000000  1.000000e+00  ...              0.000000e+00   
50%     99.000000  1.000000e+01  ...              0.000000e+00   
75%    100.000000  5.700000e+01  ...              0.000000e+00   
max    100.000000  7.480813e+06  ...              1.462997e+06   

       average_playtime_2weeks  median_playtime_forever  \
count             98528.000000             9.852800e+04   
mean                  4.860507             1.089462e+02   
std                 174.743647             8.401065e+03   
min                   0.000000             0.000000e+00   
25%                   0.000000             0.000000e+00   
50%                   0.000000             0.000000e+00   
75%                   0.000000             0.000000e+00   
max               18568.000000             1.462997e+06   

       median_playtime_2weeks      discount      peak_ccu  pct_pos_total  \
count            98528.000000  98528.000000  9.852800e+04   98528.000000   
mean                 5.111207      4.146385  9.216774e+01      45.546434   
std                182.758018     15.826629  5.456588e+03      40.752929   
min                  0.000000      0.000000  0.000000e+00      -1.000000   
25%                  0.000000      0.000000  0.000000e+00      -1.000000   
50%                  0.000000      0.000000  0.000000e+00      60.000000   
75%                  0.000000      0.000000  0.000000e+00      84.000000   
max              18568.000000    100.000000  1.212356e+06     100.000000   

       num_reviews_total  pct_pos_recent  num_reviews_recent  
count       9.852800e+04    98528.000000        98528.000000  
mean        1.312768e+03        5.283899           14.998457  
std         3.400242e+04       22.430301          425.917775  
min        -1.000000e+00       -1.000000           -1.000000  
25%        -1.000000e+00       -1.000000           -1.000000  
50%         1.500000e+01       -1.000000           -1.000000  
75%         8.100000e+01       -1.000000           -1.000000  
max         8.632939e+06      100.000000        96473.000000  

[8 rows x 21 columns]

In [ ]:
#Beziehung zwischen mittlerer Spielzeit und User Score
fig = px.scatter(
    df,
    x="average_playtime_forever",
    y="user_score",
    title="Beziehung zwischen mittlerer Spielzeit und User Score",
    labels={"average_playtime_forever": "Mittlere Spielzeit (Minuten)", "user_score": "User Score"},
    opacity=0.5,
    log_x=True
)
fig.show()

In [ ]:
#Preis vs. mittlere Spielzeit
fig1 = px.scatter(
    df, x="price", y="user_score",
    title="Preis vs. User Score",
    labels={"price": "Preis", "user_score": "User Score"},
    opacity=0.5
)
fig1.show()

fig2 = px.scatter(
    df, x="price", y="average_playtime_forever",
    title="Preis vs. mittlere Spielzeit",
    labels={"price": "Preis", "average_playtime_forever": "Mittlere Spielzeit (Minuten)"},
    opacity=0.5, log_y=True
)
fig2.show()

In [ ]:
#Mittlere Spielzeit nach Genre
def parse_genre_list(x):
    try:
        if isinstance(x, str):
            genres = ast.literal_eval(x)
            if isinstance(genres, list) and len(genres) > 0:
                return genres[0]
            elif isinstance(genres, str):
                return genres
        return None
    except (ValueError, SyntaxError):
        return None

df["main_genre"] = df["genres"].apply(parse_genre_list)
df = df.dropna(subset=["main_genre"])

genre_playtime = (
    df.groupby("main_genre")["average_playtime_forever"]
    .mean()
    .sort_values(ascending=False)
    .head(15)
)

fig = px.bar(
    x=genre_playtime.index,
    y=genre_playtime.values,
    title="Mittlere Spielzeit nach Genre",
    labels={"x": "Genre", "y": "Mittlere Spielzeit (Minuten)"},
)
fig.update_layout(xaxis_tickangle=45)
fig.show()

In [ ]:
#Mittlere Peak CCU vs. Mittlere Spielzeit nach Genre
genre_ccu = df.groupby("main_genre")["peak_ccu"].mean()
genre_players = df.groupby("main_genre")["average_playtime_forever"].mean()

fig = px.scatter(
    x=genre_ccu,
    y=genre_players,
    labels={"x": "Mittlere Peak CCU", "y": "Mittlere Spielzeit (Minuten)"},
    title="Mittlere Peak CCU vs. Mittlere Spielzeit nach Genre"
)
fig.show()

In [ ]:
#Mittlere Spielzeit nach Veröffentlichungsjahr
df["release_date"] = pd.to_datetime(df["release_date"], errors="coerce")
df["release_year"] = df["release_date"].dt.year

year_playtime = (
    df.groupby("release_year")["average_playtime_forever"]
    .mean()
    .dropna()
)

fig = px.line(
    x=year_playtime.index,
    y=year_playtime.values,
    markers=True,
    title="Mittlere Spielzeit nach Veröffentlichungsjahr",
    labels={"x": "Veröffentlichungsjahr", "y": "Mittlere Spielzeit (Minuten)"}
)
fig.show()

C:\Users\silva\AppData\Local\Temp\ipykernel_7972\2060601895.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\silva\AppData\Local\Temp\ipykernel_7972\2060601895.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
# Achievements vs mittlere Spielzeit
fig = px.scatter(
    df,
    x="achievements",
    y="average_playtime_forever",
    title="Achievements vs. mittlere Spielzeit",
    labels={"achievements": "Anzahl der Achievements", "average_playtime_forever": "Mittlere Spielzeit (Minuten)"},
    opacity=0.5,
    log_x=True,
    log_y=True
)
fig.show()

df["is_free"] = df["price"] == 0

fig1 = px.box(df, x="is_free", y="user_score", title="User Score nach frei oder bezahlt")
fig1.show()

fig2 = px.box(df, x="is_free", y="average_playtime_forever", title="Mittlere Spielzeit nach frei oder bezahlt")
fig2.show()

C:\Users\silva\AppData\Local\Temp\ipykernel_7972\460152838.py:15: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
#Anzahl der Spiele pro Jahr für Genres
genres_of_interest = ["Action", "Indie", "RPG", "Strategy"]
df_g = df[df["main_genre"].isin(genres_of_interest)].dropna(subset=["release_year"])

count_per_year = (
    df_g.groupby(["release_year", "main_genre"])
    .size()
    .unstack(fill_value=0)
    .sort_index()
)

fig = px.line(
    count_per_year,
    x=count_per_year.index,
    y=count_per_year.columns,
    title="Anzahl der Spiele pro Jahr für ausgewählte Genres",
    labels={"value": "Anzahl der Spiele", "release_year": "Veröffentlichungsjahr"}
)
fig.show()

In [ ]:
# Histogram der Preise
fig = px.histogram(
    df,
    x="price",
    nbins=100,
    title="Histogramm: Spielpreise",
    labels={"price": "Preis"},
)
fig.show()

In [ ]:
# geschätzte Besitzer nach Genre
def parse_estimated_owners_range(x):
    if isinstance(x, str):
        m = re.match(r'\s*([\d,]+)\s*-\s*([\d,]+)', x)
        if m:
            low = float(m.group(1).replace(",", ""))
            high = float(m.group(2).replace(",", ""))
            return (low, high, (low + high) / 2.0)
        clean = x.replace(",", "").strip()
        if clean.isdigit():
            v = float(clean)
            return (v, v, v)
    return (np.nan, np.nan, np.nan)

df_exp = df.copy()
df_exp["genre_list"] = df_exp["genres"].apply(parse_genre_list)
df_exp = df_exp.explode("genre_list").dropna(subset=["genre_list"])

df_exp[["est_low", "est_high", "est_mean"]] = pd.DataFrame(
    df_exp["estimated_owners"].apply(parse_estimated_owners_range).tolist(), index=df_exp.index
)

genre_stats = df_exp.groupby("genre_list", as_index=False).agg(
    est_mean_sum=("est_mean", "sum"),
    est_low_sum=("est_low", "sum"),
    est_high_sum=("est_high", "sum")
)
genre_stats["err_minus"] = genre_stats["est_mean_sum"] - genre_stats["est_low_sum"]
genre_stats["err_plus"] = genre_stats["est_high_sum"] - genre_stats["est_mean_sum"]
genre_stats = genre_stats.sort_values("est_mean_sum", ascending=False).head(15)

fig = go.Figure(
    data=[
        go.Bar(
            x=genre_stats["genre_list"],
            y=genre_stats["est_mean_sum"],
            error_y=dict(
                type="data",
                symmetric=False,
                array=genre_stats["err_plus"],
                arrayminus=genre_stats["err_minus"],
                color="black"
            ),
            marker_color="skyblue"
        )
    ]
)
fig.update_layout(
    title="Estimated owners by genre (with error bars)",
    xaxis_title="Genre",
    yaxis_title="Estimated owners (sum of means)",
    xaxis_tickangle=45
)
fig.show()